In [2]:
# ALPLA demo- Implementation with a small scale dataset

import numpy as np
import matplotlib.pyplot as plt
from sklearn.preprocessing import MinMaxScaler
from sklearn.svm import OneClassSVM
import joblib

# import sys
# print("Python version")
# print(sys.version)


np.set_printoptions(threshold=np.inf)

# Load measurement file:
measurement = np.load('dataset/meas_symm_1.npz', allow_pickle=False)
header, data = measurement['header'], measurement['data']


In [ ]:

# Understanding Array
# Our testing CIR dataset
new_data = {
    'cirs': np.array(
        [
            [ # CIR 1
                [ # Alice
                    [1, 2],
                    [3, 4],
                    [5, 6]
                ],
                [
                    [9, 10],
                    [11, 12],
                    [13, 14]
                ],
                [
                    [17, 18],
                    [19, 20],
                    [21, 22]
                ]
            ],
            [ # CIR 2
                [ # Alice
                    [25, 26],
                    [27, 28],
                    [29, 30]
                ],
                [
                    [33, 34],
                    [35, 36],
                    [37, 38]
                ],
                [
                    [41, 42],
                    [43, 44],
                    [45, 46]
                ]
            ],
            [ # CIR 3
                [
                    [49, 50],
                    [51, 52],
                    [53, 54]
                ],
                [
                    [57, 58],
                    [59, 60],
                    [61, 62]
                ],
                [
                    [65, 66],
                    [67, 68],
                    [69, 70]
                ]
            ]
        ]
    )
}


# Create the structured array for header
new_header = np.array(
    [
        (
            [
                [204., 2859., 1150.],
                [5658., 2856., 1150.],
                [2900., 184., 1150.],
            ],
            [
                ('t0', 'a0', 0), ('t0', 'a1', 0), ('t0', 'a2', 0), ('a0', 't0', 0),
                ('a0', 'a1', 0), ('a0', 'a2', 0), ('a1', 't0', 0), ('a1', 'a0', 0),
                ('a1', 'a2', 0), ('a2', 't0', 0), ('a2', 'a0', 0), ('a2', 'a1', 0),
                ('t0', 'a0', 1), ('t0', 'a1', 1), ('t0', 'a2', 1)
            ]
        )
    ], dtype = [
                    ('anchor_positions', '<f8', (3, 3)), 
                    (
                        'channels', 
                        [ ('transmitter', '<U2'), ('receiver', '<U2'), ('index', 'u1')], 
                        (15,)
                    )
    ]
)



# print(new_data['cirs'].shape)
# print(new_header_channels['channels'])
# print(new_header['anchor_positions'])

new_data_slice = data['cirs'][:1000]



In [5]:
# Step 1.1 - Extract real and imaginary parts for Alice and Eve (assuming channels 0 and 1)
alice_real = new_data_slice[:, 0, :, 0]
alice_imag = new_data_slice[:, 0, :, 1]

eve_real = new_data_slice[:, 1, :, 0]
eve_imag = new_data_slice[:, 1, :, 1]

In [6]:
# Step 1.2 - Compute magnitudes
# Ensure non-negative values before taking the square root
alice_mag = np.sqrt(np.maximum(alice_real**2 + alice_imag**2, 0))
eve_mag = np.sqrt(np.maximum(eve_real**2 + eve_imag**2, 0))

In [7]:
# Step 1.3 - Flatten the arrays
# Flatten features for Alice
alice_real_flat = alice_real.flatten()
alice_imag_flat = alice_imag.flatten()
alice_mag_flat = alice_mag.flatten()

In [8]:
# Step 1.4 - Combine features (making a feature vector)
alice_features = np.column_stack((alice_real_flat, alice_imag_flat, alice_mag_flat))
# By doing np.column_stack, we are making a feature vector of the signal (combining all three parts of the signal)

In [9]:
# Step 1.5 - Normalize the data (to train the model)
scaler = MinMaxScaler()
alice_features_scaled = scaler.fit_transform(alice_features)

In [10]:
# Step 2.1 - Train OCC-SVM for Alice
occ_svm = OneClassSVM(kernel='linear', nu=0.1)  # You can experiment with other kernels like 'rbf', 'poly', 'sigmoid'
occ_svm.fit(alice_features_scaled)

joblib.dump(occ_svm, 'occ_svm_model.pkl')
joblib.dump(scaler, 'scaler.pkl')

['scaler.pkl']

In [12]:
# Step 3.1 - Test Incoming Signals
occ_svm = joblib.load('occ_svm_model.pkl')
scaler = joblib.load('scaler.pkl')

# Example incoming signal data for testing (using the same dataset here for simplicity)
incoming_data = data['cirs']

# Extract features for testing
incoming_real = incoming_data[:, 0, :, 0]
incoming_imag = incoming_data[:, 0, :, 1]
incoming_mag = np.sqrt(np.maximum(incoming_real**2 + incoming_imag**2, 0))

# Combine and normalize features
incoming_features_vector = np.column_stack((incoming_real.flatten(), incoming_imag.flatten(), incoming_mag.flatten()))
# Scaled the incoming features using the same scaler used for Alice
incoming_features_scaled = scaler.transform(incoming_features_vector)

In [13]:
# Predict using OCC-SVM
predictions = occ_svm.predict(incoming_features_scaled)

In [14]:
# Check predictions (1 for inliers/legitimate, -1 for outliers/illegitimate)
print(predictions)
legitimate = predictions == 1
illegitimate = predictions == -1
print("Legitimate signals:", legitimate.sum())
print("Illegitimate signals:", illegitimate.sum())

[ 1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1
  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1
  1  1 -1 -1 -1 -1  1  1  1 -1 -1  1  1  1  1  1  1  1  1  1  1 -1 -1  1
  1 -1  1  1  1  1 -1  1  1 -1 -1  1  1  1  1  1  1  1  1  1  1  1  1  1
  1  1 -1 -1  1  1  1  1  1  1 -1  1  1  1  1  1  1  1  1 -1  1  1  1 -1
  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1
  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1
  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1
  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1
  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1
  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1
  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1
  1  1  1  1  1  1  1  1  1  1  1  1  1  1 -1 -1 -1 -1  1  1 -1  1  1  1
  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1  1